Ampliación de Matemátcias. Aproximación de raíces. 

Por Pablo Angulo y Fabricio Macià para ETSIN@UPM.

# Aproximación de raíces, puntos fijos y optimización de funciones en una variable

Vamos a practicar diversas técnicas para encontrar ceros (raíces) de funciones no lineales de una variable real.

Comenzamos por un ejemplo sencillo:
$$
f(x) = x + \frac{1}{2}\sin(x) -1.
$$

 - Dibujemos la función cuyas raíces queremos calcular.

In [ ]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
import scipy.optimize
from scipy.optimize import minimize_scalar, bisect, newton


In [ ]:
def f(x):
    return x + np.sin(x)/2 - 1

xmin = -5
xmax = 5
xs = np.linspace(xmin, xmax,200)
ys = f(xs)
plt.figure(figsize=(8,8))
plt.plot(xs, ys)
plt.title('Gráfica de f')
plt.xlabel('x')
plt.ylabel('y')
plt.axhline(color='k')
plt.show()

Observar las funciones nos puede dar pistas sobre el número y ubicación aproximada de las raíces, pero necesitamos demostrar la existencia y unicidad con alguna de estas técnicas:

 - Si la función es continua, y en un intervalo cambia de signo, tiene que haber una raíz en ese intervalo (_teorema de Bolzano_).
 - Si en un intervalo la derivada no cambia de signo, no puede haber más de una raíz (consecuencia del _teorema de Rolle_).

En este caso concreto, tenemos un cambio de signo en el intervalo (-1,1), luego hay una raíz de $f$:

In [ ]:
f(-1), f(1)

In [ ]:
plt.figure(figsize=(9,6))
plt.plot(xs,ys)
xleft = -1
xright = 1

plt.plot([xleft, xright], [0,0], 'o')
plt.axhline(color='k')
plt.show()

La derivada de $f$ es fácil de calcular:
$$
f'(x) = 1 + \frac{1}{2}\cos(x)
$$
y podemos acotarla fácilmente por debajo si escribimos:
$$
1 = f'(x) - \frac{1}{2}\cos(x)
$$
y usando la desigualdad triangular:
$$
1 \leq |f'(x)| + \frac{1}{2}|\cos(x)|
$$
luego
$$
|f'(x)| \geq 1 - \frac{1}{2}|\cos(x)| \geq 1 - \frac{1}{2} =  \frac{1}{2} > 0
$$
Es decir, $f'$ no se anula nunca. Como $f'(0)>0$ y $f'$ no cambia de signo, $f'$ siempre es positiva, luego $f$ es creciente en todo $\mathbb{R}$, luego $f$ tiene sólo una raíz.

Ahora bien, encontrar esa raíz de forma exacta no es posible, y nos tenemos que contentar con aproximarla.


## Método de la bisección

 - OBJETIVO: Encontrar un intervalo [x1, x2] tal que hay una raíz x* de f en ese intervalo.
 - INICIO: Partimos de un intervalo `[xleft, xright]` donde $f$ cambia de signo.
 - REPITE: Evalúa $f$ en `xmed = (xleft + xright)/2`. Nos quedamos con un nuevo intervalo donde hay un cambio de signo y de longitug la mitad que el anterior.
 - HASTA QUE: Terminamos cuando el intervalo obtenido tenga longitud menor que `xtol`.

In [ ]:
plt.figure(figsize=(9,6))
plt.plot(xs,ys)

xleft  = -4
xright = 4
xtol = 1e-2
plt.plot([xleft], [ 0], 'x', label='left end')
plt.plot([xright], [0], 'x', label='right end')


j = 1
sleft  = np.sign(f(xleft))
sright = np.sign(f(xright))
while xright - xleft > xtol:
    xmed = (xleft + xright)/2
    smed = np.sign(f(xmed))
    if smed==sleft:
        xleft = xmed
    else:
        xright = xmed
    plt.plot([xmed], [0], 'o', label='step %d'%j)
    j = j + 1

plt.legend()
plt.axhline(color='k')
plt.show()

## Error en el método de la bisección

Recuerda que en cada paso del método de la bisección obtenemos un nuevo valor $x_n$ (el punto medio del intervalo que se subdivide), que pasa a ser uno de los extremos del nuevo intervalo que se subdividirá en la etapa siguiente. 

Por ejemplo, en la primera iteración 

$$
x_1=\frac{a+b}{2}.
$$

El error en la iteración $n$ es: 

$$
e_n=x_n-x_*,\quad \text{ siendo } f(x_*)=0.
$$

Sabemos, por como se han construido las iteraciones,  que:

$$
|e_n|\leq \frac{b-a}{2^n};
$$

en particular, esto sugiere que el error en la etapa $n+1$ y el error en la etapa $n$ se relacionan por:

$$
|e_{n+1}| \approx \frac{1}{2}|e_n|.
$$



Ventajas:
- Siempre converge.

Inconvenientes:
- Sólo se puede aplicar si tenemos dos aproximaciones de la raíz en las que $f$ toma valores de signo opuesto (inconveniente menor).
- Suele converger más lentamente que otros métodos (inconveniente mayor).

### Ejercicio

Empaqueta el método de bisección como una función con entradas:

 - Una función `f` continua
 - Los extremos de un intervalo `a` y `b`.
 - Una tolerancia para el error `xtol`

y salidas

 - Si `f(a)*f(b)>0`, se rompe y no devuelve nada (imprime un mensaje de error, lanza una "excepción", etc)
 - Si `f(a)*f(b)<=0`, devuelve un valor que dista de la raíz de `f` menos que `xtol` y un array con todas las aproximaciones sucesivas a la raiz. 

### Ejercicio

Utilizando la función que has construido en el ejercicio anterior, representa gráficamente el error $e_n$ cometido en cada iteración y el cociente $e_{n+1}/e_n$ con el método de la bisección aplicado a la función:

$$
f(x) = x + \frac{1}{2}\sin(x) -1,\quad \text{ con } a=-4, \; b=4.
$$

### Ejercicio

- Busca ahora las raíces de 

$$
f(x) = x^3 - 4x + \log(1+x^2)
$$
  Atención: ¿hay más de una raíz? ¿cuántas son positivas?

In [ ]:
def f(x):
    return (x**3 - 4*x) + np.log(1+x**2)

xmin = -3
xmax = 3

### Ejercicio

 - Busca una función de la librería `scipy.optimize` que implementa el algoritmo de bisección, compara sus argumentos, la forma de reportar el resultado y su comportamiento en caso de argumentos incorrectos con la función que has creado un poco más arriba.
 - Compara el resultado de esta función con la tuya en uno de los ejemplos anteriores.
 
Os recomendamos usar los dos métodos principales para encontrar información sobre una librería:
 - Buscar en la documentación de la librería:
     + si ya hemos importado `scipy.optimize`, escribimos `scipy.optimize.` y pulsando el tabulador muestra los métodos de esa librería. Podemos escribir algunas letras para limitar la búsqueda a los métodos que empiezan con `b`, por ejemplo.
     + Una interrogación al final de un identificador, por ejemplo `scipy.optimize.bisect?`, muestra la ayuda sobre ese objeto.
 - Buscar en internet, por ejemplo _"scipy bisection method"_.

## Método de la secante

El método de la secante, al igual que el método de la bisección, arranca eligiendo dos puntos $x_0,x_1$ que intuimos son una buena aproximación de la raíz $x_*$ de la ecuación

$$
f(x)=0
$$

que queremos encontrar. Pero, al contrario que en el método de la bisección, la raíz no tiene por qué estar en el intervalo $[x_0,x_1]$.

El algoritmo produce una sucesión de aproximaciones $x_2,x_3,\dots,x_n$ a la raíz del siguiente modo:

- Elegimos como $x_2$ la raíz de la recta que pasa por $(x_0, f(x_0))$ y $(x_1,f(x_1))$. En otras palabras, reemplazamos $f$ por su *interpolación lineal* (hablaremos de esto en el siguiente capítulo) por los puntos $x_0$ y $x_1$. Dicha recta tiene por ecuación:

$$
y = \left(\frac{f(x_1) - f(x_0)}{x_1-x_0}\right) (x - x_1) + f(x_1).
$$

Su raíz es el valor de $x$ que cumple

$$
y=0=\left(\frac{f(x_1) - f(x_0)}{x_1-x_0}\right) (x - x_1) + f(x_1),
$$

por tanto,

$$
x_2:= x_1 - \frac{f(x_1)}{f(x_1)-f(x_0)}(x_1-x_0).
$$

- En general, para $n\geq$ calculamos $x_n$ a partir de $x_{n-1}$ y $x_{n-2}$:

$$
x_n:= x_{n-1} - \frac{f(x_{n-1})}{f(x_{n-1})-f(x_{n-2})}(x_{n-1}-x_{n-2}).
$$


Ventajas:
 - Cuando converge, lo hace más deprisa que el método de la secante.
 
Inconvenientes:
 - No siempre converge.

### Ejercicio

Implementa el método de la secante:
 - ¿Qué argumentos necesita?
 - ¿Qué criterio de parada vas a elegir?
 

## Método de la *regula falsi* o falsa posición

- Es una combinación del método de la bisección y de la secante. 
- Es idéntico al método de la bisección; pero en lugar de elegir el punto medio del intervalo, elegimos la raíz a de la recta secante a la gráfica de la función por los extremos del intervalo.

Esta filosofía da lugar a los **métodos híbridos** que se utilizan en la práctica, como el **método de Brent**.

## Método del punto fijo

Este método consiste en escribir la ecuación

$$
f(x)=0,
$$

en la forma

$$
x=g(x);
$$

un punto que verifica la ecuación anterior es un **punto fijo** de la función $g$.

No todas las funciones tienen puntos fijos, pero hay dos casos en que podemos garantizar que es así:

- Si $g:[a,b]\rightarrow [a,b]$ (la función $g$ manda cualquier punto del intervalo $[a,b]$ en otro punto del *mismo* intervalo $[a,b]$) es una función continua entonces $g$ tiene un punto fijo en el intervalo $[a,b]$.
- Si $g:[a,b]\rightarrow [a,b]$ **y además** 
$$
|g'(x)|\leq k < 1, \quad\text{para cualquier } x \text{ en } [a,b], 
$$ 
entonces hay un único punto fijo en el intervalo $[a,b]$.


En el ejemplo anterior, la ecuación

$$
f(x) = x + \frac{1}{2}\sin(x) -1=0,
$$

se puede escribir como:

$$
x=1-0.5\, \sin(x), 
$$

que tiene la estructura de ecuación de punto fijo con 

$$
g(x)= 1-0.5\, \sin(x).
$$

El método del punto fijo consiste en:

 - comenzar con una aproximación (grosera) $x_0$ del punto fijo, bien elegida al azar, o construida por otros métodos (bisección, por ejemplo).
 - construir aproximaciones sucesivas de la forma:

$$
x_{n+1}=g(x_n),
$$
 - hasta que la diferencia entre $x_n$ y $x_{n+1}$ es más pequeña que nuestra tolerancia.


Si $g'(x)$, la derivada de $g$, es pequeña cerca del punto fijo (esto quiere decir que $g(x)$ no tiene variaciones abruptas cerca del punto fijo), entonces las aproximaciones $x_n$ se van acercando al punto fijo a medida que $n$ crece.

Más precisamente: 
- si $x_*=g(x_*)$ y $|g'(x)|<1$ para $x$ variando dentro de un intervalo $(x_*-\delta,x_*+\delta)$, 
- la primera aproximación $x_0$ se encuentra en ese mismo intervalo $(x_*-\delta,x_*+\delta)$,

entonces el error:

$$
e_n=x_n-x_*
$$

tiende a cero cuando n$\to\infty$. 

## Error del método de punto fijo

Además, 

$$
\frac{|e_{n+1}|}{|e_n|}\to |g'(x_*)|,\quad \text{ cuando }n\to \infty.
$$

En otras palabras, 

$$
|e_{n+1}|\approx |g'(x_*)| |e_n|.
$$

Además, 

$$
|e_n|=|x_n-x_*|=|g(x_{n-1})-g(x_*)|=\underbrace{|g'(\zeta_n)|}_{\zeta_n\text{ entre }x_{n-1}\text{ y }x_*}|x_{n-1}-x_*|\leq k|e_{n-1}|,
$$

de lo que se deduce que:

$$
|e_n|\leq k^n |e_0|. 
$$

Por otra parte,

$$
|x_{n+1}-x_n|=|g(x_n)-g(x_{n-1})|=\underbrace{|g'(\zeta_n)|}_{\zeta_n\text{ entre }x_n\text{ y }x_{n-1}}|x_{n}-x_{n-1}|.
$$

Aplicando esto $n$ veces obtenemos:

$$
|x_{n+1}-x_n|=|g(x_n)-g(x_{n-1})|\leq k|x_{n}-x_{n-1}|\leq\dots\leq k^n |x_1-x_0|,
$$

de lo que se deduce, con un poco más de esfuerzo (pregunta si no te sale), que 
$$
|e_n|< \frac{k^n}{1-k}|x_1-x_0|.
$$


### Convergencia cuadrádica

¿Qué ocurre cuando $|g'(x_*)|=0$?

En este caso, la velocidad de convergencia es mayor. Para ver por qué, procedemos como antes; pero en esta ocasión hacemos un desarrollo de Taylor de $g(x)$ en $x=x_*$ hasta orden dos:

$$
e_{n+1} = x_{n+1}-x_*=g(x_n) - g(x_*) = g'(x_*)(x_n - x_*)+ \underbrace{\frac{g''(\zeta_n)}{2}}_{\zeta_n\text{ entre }x_n \text{ y }x_{*}}(x_n-x_*)^2;
$$

como $g'(x_*)=0$ esto implica:

$$
e_{n+1} = \frac{g''(\zeta_n)}{2}(e_n)^2.
$$

Por tanto, si $e_n$ converge a cero se cumple

$$
\frac{e_{n+1}}{(e_n)^2}\to \frac{|g''(x_*)|}{2},\quad \text{ cuando } n\to\infty.
$$

En otras palabras, $e_n$ va a cero cuadráticamente:

$$
|e_{n+1}|\approx \frac{|g''(x_*)|}{2} |e_n|^2.
$$

Ventajas:
- Es fácil de implementar.

Inconvenientes:
- No hay garantía de que la elección que hagamos de $x_0$ de lugar a una sucesión de aproximaciones de el punto fijo $x_*$. Incluso cuando $|g'(x)|<1$ en un entorno de $x_*$ uno tiene que asegurarse de que $x_0$ está lo suficientemente cerca de $x_*$.
- Si $|g'(x_*)|>1$ las aproximaciones **no convergen**.

### Ejercicio

Empaqueta el método de del punto fijo como una función con entradas:

 - Una función `g` continua
 - Una aproximación inicial `x_O`
 - Un número máximo de iteraciones `N`
 - Una tolerancia para el error `tol` (parámetro opcional, por defecto `1.e-6`)

y salidas

 - Si se llega al número de iteraciones `N`o el valor absoluto de `x-g(x)` es menor que `tol` se devuelve la última iteración.

### Ejercicio

Sea $f(x) = x - e^{-x}$, vamos a resolver $f(x) = 0$

- Escribiéndola como la ecuación de punto fijo $x = e^{-x}$ ($x = g(x)$ con $g(x) = e^{-x}$).
- Escribiéndola como la ecuación de punto fijo $x = -\ln x$.

Comprueba que ambas formulaciones son equivalentes.

Utiliza el método de punto fijo para cada una de las formulaciones, utilizando varias aproximaciones iniciales ¿Podrías explicar lo que sucede? 

## Método de Newton

Nuevamente, vamos a resolver una ecuación de la forma

$$
f(x)=0.
$$

Si tomamos una aproximación $x_n$, es poco probable que $f(x_n)=0$.  No obstante, uno puede esperar que exista una corrección $\delta_n$ de forma que
$$x_{n+1} = x_n + \delta_n$$
satisfaga
$$
    f(x_{n+1}) = 0. 
$$

Hagamos una expansión de Taylor en torno a $x_n$: 

$$
    f(x_n + \delta_n) =  f(x_n) + f'(x_n) \delta_n  + O((\delta_n)^2).
$$

Si sustituimos por esta expresión en $f(x_{n+1})=0$ y despreciamos los términos cuadráticos en $\delta_n^2$ llegamos a:

$$
    f(x_n) + f'(x_n) \delta_n  =0;
$$

Despejando, obtenemos:

$$
\delta_n=-\frac{f(x_n)}{f'(x_n)}.
$$

Por tanto,

$$
x_{n+1} = x_n -\frac{f(x_n)}{f'(x_n)}.
$$

## Error en el método de Newton

El método de Newton puede interpretarse como una iteración de punto fijo
$$
x=g(x)
$$
asociada a la función
$$
g(x)=x - \frac{f(x)}{f'(x)}.
$$
Un cálculo inmediato muestra que, siempre que $f'(x)\neq 0$ y exista la segunda derivada $f''(x)$ se tiene:
$$
g'(x)=\frac{f(x)f''(x)}{(f'(x))^2}.
$$


Así pues, si $f(x_*)=0$ entonces $g'(x_*)=0$. Hemos visto que el error 
$$
e_n=x_n-x_*
$$
entonces satisface
$$
\frac{e_{n+1}}{e_n}\to 0, \quad\text{ cuando } n\to \infty.
$$

Esto quiere decir que $e_{n+1}$ es mucho más pequeño que $e_n$ (para el método de punto fijo teníamos que $e_{n+1}$ era asintóticamente proporcional proporcional a $e_n$, siendo el factor de proporcionalidad el valor de la derivada en $x_*$).

Esto se puede precisar, de hecho:

$$
\frac{|e_{n+1|}}{|e_n|^2}\to c, \quad\text{ cuando } n\to \infty
$$

para cierta constante $c \geq 0$.

Decimos que el orden de convergencia del método es **cuadrático**, mucho más rápido que en el caso de la bisección o el punto fijo (en ese caso el orden es **lineal**).

No obstante no podemos a priori saber si el método converge o no. Para ello la iteración inicial $x_0$ debe estar suficientemente cerca de la raíz exacta $x_*$, y se tiene que verificar la condición
$$
|g'(x)|=\left|\frac{f(x)f''(x)}{(f'(x))^2}\right|<1,
$$
en el intervalo cuyos extremos son $x_0$ y $x_*$. Esto es difícil de comprobar en la práctica.

## Implementación del método de Newton

Como no tenemos garantía de éxito, debemos programar nuestro método de forma defensiva. Si escribimos por ejemplo:
```python
def metodo_newton(f, fp, x0, ytol):
    x = x0
    error = np.abs(f(x))
    while error > ytol:
        x = x - f(x)/fp(x)
        error = np.abs(f(x))
    return x
```
nos encontraremos en un bucle infinito siempre que el método no converja.

Una forma de evitar este problema es imponer un máximo de iteraciones usando un contador:
```python
def metodo_newton(f, fp, x0, ytol, maxiter=100):
    x = x0
    error = np.abs(f(x))
    k = 0 #contador
    #el bucle se detiene cuando se consiga la precisión deseada,
    #  pero también termina prematuramente si
    #  se alcanza el máximo de iteraciones
    while error > ytol and k<maxiter:
        x = x - f(x)/fp(x)
        error = np.abs(f(x))
        k = k + 1
    return x
```

En la definición anterior hemos usado el __criterio de parada__ $|f(x_n)|<ytol$.

El otro criterio de parada habitual es $|x_{n+1}-x_n|<xtol$ o utilizando el error relativo:

$$
|x_{n+1}-x_n|<xtol|x_n|.
$$

El código que corresponde a ese criterio de parada es:

```python
def metodo_newton(f, fp, x0, xtol, maxiter=100):
    x = x0
    #Comenzamos con un error infinito, simplemente para que
    #la ejecución del programa no se detenga antes de empezar
    errorx = np.inf
    k = 0 #contador
    #el bucle se detiene cuando se consiga la precisión deseada,
    #  pero también termina prematuramente si
    #  se alcanza el máximo de iteraciones
    while error > xtol and k<maxiter:
        xnew = x - f(x)/fp(x)
        error = np.abs(xnew - x)
        x = xnew
        k = k + 1
    return x
```

Finalmente, ya que no hay garantías de éxito, es interesante devolver no sólo nuestra estimación de la raíz, sino nuestra estimación de la precisión obtenida:

```python
def metodo_newton(f, fp, x0, xtol, maxiter=100):
    x = x0
    #Comenzamos con un error infinito, simplemente para que
    #la ejecución del programa no se detenga antes de empezar
    errorx = np.inf
    k = 0 #contador
    #el bucle se detiene cuando se consiga la precisión deseada,
    #  pero también termina prematuramente si
    #  se alcanza el máximo de iteraciones
    while errorx > xtol and k<maxiter:
        xnew = x - f(x)/fp(x)
        errorx = np.abs(xnew - x)
        x = xnew
        k = k + 1
    return x, errorx
```

In [ ]:
def metodo_newton(f, fp, x0, xtol, maxiter=100):
    x = x0
    #Comenzamos con un error infinito, simplemente para que
    #la ejecución del programa no se detenga antes de empezar
    errorx = np.inf
    k = 0 #contador
    #el bucle se detiene cuando se consiga la precisión deseada,
    #  pero también termina prematuramente si
    #  se alcanza el máximo de iteraciones
    while errorx > xtol and k<maxiter:
        xnew = x - f(x)/fp(x)
        errorx = np.abs(xnew - x)
        x = xnew
        k = k + 1
    return x, errorx

In [ ]:
f = lambda x: x**2-2
fp = lambda x: 2*x

# 2 iteraciones son insuficientes para conseguir la precisión deseada
print(metodo_newton(f,fp, 1, 1e-8, 2))
# 10 iteraciones sí son suficientes para conseguir la precisión deseada
# La estimación del error es mejor que la precisión mínima que le pedimos
print(metodo_newton(f,fp, 1, 1e-8, 10))
print(metodo_newton(f,fp, 1, 1e-8, 100))

### Calcular derivadas mediante cálculo simbólico

Para el método de Newton, y para muchos otros, es necesario poder evaluar la derivada de una función. Nuestras opciones son:
 - Podemos calcular la derivada a mano, aunque:
     + es fácil equivocarse si el cálculo es largo.
     + no se puede automatizar: al cambiar la función hay que derivar de nuevo.
 - Podemos usar derivación numérica, de la que hablaremos más adelante.
 - Podemos usar cálculo simbólico, que siempre consigue calcular la derivada de una función. Es fácil encontrar ejemplos en internet: ¿conseguirás ser el primero en subir un ejemplo al foro? Los profesores comentarán después tu solución...
 - Podemos buscar otro método que no necesite el cálculo de la derivada. De entre los métodos que hemos visto: ¿cuál es el método que más se parece al método de Newton y que no necesita el cálculo de la derivada?

### Ejercicio

 - Escribe la documentación (_'docstring'_) de la función `metodo_newton`.
 - Compara el método de Newton con el de bisección en los ejemplos anteriores. Constata la importancia de una buena primera aproximación. Compara el número de iteraciones necesarias para conseguir la misma precisión con uno y otro método.

### Ejercicio

Aplica ahora el método de Newton para resolver la ecuación:

$$
    f(x) = x^2 + x - \sin(x)=0
$$

Toma por ejemplo como aproximación inicial $x_0=0.9$. Compara la velocidad a la que el error tiende a cero para este ejemplo y los ejemplos anteriores. ¿Observas alguna diferencia? ¿A qué puede ser debido esto?

## Resumen: métodos de Newton y Secante en una variable

 - El método de **Newton** busca raíces de f(x), iterando 
$$x_{n+1}=x_{n} - \frac{f(x_n)}{f'(x_{n})}$$
    - Es una iteración de punto fijo, con $g(x) = x - f(x)/f'(x)$.
    - No es fácil saber si convergerá... pero cuando lo hace es de orden 2
    - Hay que evaluar la derivada
 - El método de la **secante** es similar al de Newton, salvo porque se sustituye la derivada $f'(x)$ por el cociente incremental:
$$
f'(x_n)\approx \frac{f(x_{n})-f(x_{n-1})}{x_{n}-x_{n-1}}.
$$
El método resultante es: 
$$x_{n+1}=x_{n} - \frac{f(x_n)\left(x_{n}-x_{n-1}\right)}{f(x_{n})-f(x_{n-1})}$$
    - No hay que evaluar la derivada
    - El orden de convergencia es algo menor (investiga en internet cuál es el orden).

Los métodos de Newton y Secante tienen diferencias cualitativas con el método de bisección:
 - no tenemos un intervalo que acota la raíz, sino un punto que la aproxima.
 - no tenemos una cota teórica del error entre el punto $x_n$ y la raíz, a menos que se verifiquen las condiciones de convergencia y podamos acotar la segunda derivada. Tenemos dos soluciones:
     + evaluar el error en la 'y': la diferencia entre $f(x)$ y $0$.
     + estimar el error en la 'x' comparando $x_n$ con $x_{n+1}$.
 - si no conseguimos verificar las hipótesis de los teoremas de convergencia (en particular acotando $f''$), no tenemos garantía de éxito.

### Ejercicio

- Compara el método de la secante con el de Newton para calcular la raices cuadradas. Compara el número de iteraciones necesarias para conseguir la misma precisión con uno y otro método.
- * ¿Podrías estimar numéricamente el orden de convergencia del método de la secante? Es decir, encontrar (mediante experimentos numéricos) qué número $\gamma>0$ cumple que
 $$
 \frac{|e_{n+1}|}{|e_n|^\gamma}\to m>0,\quad \text{cuando }n\to\infty
 $$
siempre que la iteración converja. Si nunca has estudiado regresión, el ejercicio no es fácil, y te recomendamos que retomes el ejercicio después de estudiar regresión en este mismo curso.
 - Busca los métodos oficiales de newton y secante en `scipy.optimize`. Compara las decisiones tomadas y prueba uno y otro método en algún ejemplo concreto.